In [1]:
import os, pickle
import pandas as pd

In [2]:
import sys
sys.path.append("../../training_data")

In [3]:
from utils.utils import Cif

# Data

In [4]:
with open("../../training_data/8.Apos/Extra_set/features.pkl", "rb") as f:
    news = pickle.load(f)

len(news), news

(9,
 {'8sgj':     Residues                                                          \
           pdb label_entity_id label_asym_id label_seq_id auth_asym_id   
  0       8sgj               1             A           52            A   
  1       8sgj               1             A           53            A   
  2       8sgj               1             A           54            A   
  3       8sgj               1             A           55            A   
  4       8sgj               1             A           56            A   
  ..       ...             ...           ...          ...          ...   
  746     8sgj               1             A          941            A   
  747     8sgj               1             A          942            A   
  748     8sgj               1             A          943            A   
  749     8sgj               1             A          944            A   
  750     8sgj               1             A          945            A   
  
                       

In [5]:
with open("../../training_data/8.Apos/Extra_set/apos_sites.pkl", "rb") as f:
    news_sites = {k: [{"id": sid, "site": site["site"]} for sid, site in v.items()] for k, v in pickle.load(f).items() if k in news}

len(news_sites), news_sites

(9,
 {'8sgj': [{'id': (0, 'P32418', 'A'),
    'site':    label_comp_id label_asym_id label_entity_id label_seq_id pdbx_PDB_ins_code  \
    0            GLU             A               1          132                 ?   
    1            THR             A               1          133                 ?   
    2            VAL             A               1          134                 ?   
    3            SER             A               1          135                 ?   
    4            LEU             A               1          137                 ?   
    5            THR             A               1          138                 ?   
    6            ALA             A               1          141                 ?   
    7            HIS             A               1          200                 ?   
    8            VAL             A               1          203                 ?   
    9            VAL             A               1          206                 ?   
    10         

In [6]:
assert all(len(sites) == 1 for sites in news_sites.values()), "Not all apos have a single annotated site"

# Process structures

In [7]:
os.makedirs("structures", exist_ok=True)

In [8]:
import pymol2

In [9]:
for pdb in news:
    ciff = f"../../training_data/8.Apos/Extra_set/cifs/{pdb}.cif"
    if not os.path.isfile(f"structures/{pdb}.cif"):
        os.system(f"cp {ciff} structures/{pdb}.cif")

    if not os.path.isfile(f"structures/{pdb}.pdb"):
        with pymol2.PyMOL() as pymol:
            pymol.cmd.feedback("disable", "executive", "details")
            pymol.cmd.load(ciff, "structure")
            pymol.cmd.save(f"structures/{pdb}.pdb", "structure")

In [10]:
# !zip structures_apos.zip structures/*

# Our results

In [11]:
from autogluon.tabular import TabularDataset, TabularPredictor

In [12]:
def process_dataframe(df):
    df.index = df["Pockets"][["pdb", "pocket"]].apply(lambda x: "_".join(x), axis=1)
    df = df.drop(columns=["Pockets"], level=0)
    df.columns = map(lambda x: "_".join(x), df.columns.values)
    df.loc[:,'Label_label'] = df['Label_label'].astype("category")
    return df

## Model 5.

In [13]:
with open("../../training_data/8.Apos/Extra_set/pockets_features.pkl", "rb") as f:
    extra = pd.concat((
        pickle.load(f).values()
    ))

extra

Pockets                                              Label      FPocket  \
        pdb    pocket nres site_in_pocket pocket_in_site label Pocket Score   
0      8sgj  pocket16   12        0.00000       0.000000     0      -0.0342   
1      8sgj  pocket28   14        0.00000       0.000000     0      -0.1447   
2      8sgj  pocket18   13        0.03125       0.076923     0      -0.0508   
3      8sgj  pocket11   19        0.00000       0.000000     0       0.0417   
4      8sgj  pocket25   13        0.00000       0.000000     0      -0.1152   
..      ...       ...  ...            ...            ...   ...          ...   
265    4jqi   pocket8   14        0.20000       0.142857     0       0.0042   
266    4jqi   pocket3   16        0.00000       0.000000     0       0.2233   
267    4jqi  pocket12   12        0.00000       0.000000     0      -0.0437   
268    4jqi  pocket19   16        0.00000       0.000000     0      -0.1457   
269    4jqi   pocket6   18        0.00000       0.000000     0       0.0327   

                                                                 ...  \
    Drug Score Number of alpha spheres Mean alpha-sphere radius  ...   
0       0.3070                    53.0                   3.4745  ...   
1       0.0047                    71.0                   3.4962  ...   
2       0.0055                    45.0                   3.7490  ...   
3       0.1571                    82.0                   3.2878  ...   
4       0.0046                    58.0                   3.5925  ...   
..         ...                     ...                      ...  ...   
265     0.0047                    42.0                   3.5379  ...   
266     0.0927                    55.0                   3.4106  ...   
267     0.0029                    54.0                   3.6728  ...   
268     0.0054                    80.0                   3.7185  ...   
269     0.0099                    72.0                   3.7133  ...   

      HHBlits                                                              \
         M->M      M->I      M->D      I->M      I->I      D->M      D->D   
0    0.960393  0.013573  0.026106  0.258887  0.491092  0.049368  0.950513   
1    0.881871  0.030298  0.087796  0.383562  0.616425  0.018516  0.981423   
2    0.899622  0.030244  0.070014  0.401700  0.598274  0.106505  0.893517   
3    0.876903  0.036800  0.086349  0.289485  0.710526  0.047774  0.952233   
4    0.936656  0.023770  0.039556  0.351106  0.572006  0.165316  0.834701   
..        ...       ...       ...       ...       ...       ...       ...   
265  0.903910  0.020998  0.075087  0.359765  0.640269  0.103486  0.896543   
266  0.964962  0.009062  0.025914  0.298281  0.639198  0.224343  0.775659   
267  0.957657  0.028217  0.014108  0.418731  0.497841  0.307800  0.692181   
268  0.944717  0.018328  0.037005  0.286179  0.588822  0.091041  0.908843   
269  0.818487  0.053249  0.128251  0.364035  0.635970  0.302670  0.697328   

                                    
          Neff    Neff_I    Neff_D  
0     7.402167  0.777083  4.546750  
1     8.198214  1.068071  4.327357  
2     8.226231  1.096231  3.046538  
3    10.482684  1.128737  3.646263  
4     8.005692  1.033462  2.943231  
..         ...       ...       ...  
265  11.652929  1.203571  6.393357  
266  11.691562  1.083687  2.318750  
267  11.358750  1.477750  1.626333  
268  11.506875  1.060500  3.739063  
269  11.367500  1.758778  4.348611  

[270 rows x 194 columns]

In [14]:
extra[("Pockets", "pdb")].unique()

array(['8sgj', 'AF-A0A1D8PQM9-F1', '7l6r', '8vw5', '6yhr', '7xlq', '5b0u',
       '5uak', '4jqi'], dtype=object)

In [15]:
predictor = TabularPredictor.load("../pockets_physchem")

In [16]:
extra_probs = predictor.predict_proba( process_dataframe(extra) )
extra_probs

0             1
8sgj_pocket16  0.998758  1.241810e-03
8sgj_pocket28  0.999933  6.712489e-05
8sgj_pocket18  0.999967  3.303184e-05
8sgj_pocket11  0.998627  1.372718e-03
8sgj_pocket25  0.998793  1.207400e-03
...                 ...           ...
4jqi_pocket8   0.999994  5.881765e-06
4jqi_pocket3   0.999406  5.942771e-04
4jqi_pocket12  1.000000  3.218317e-07
4jqi_pocket19  0.999932  6.801011e-05
4jqi_pocket6   0.997571  2.429151e-03

[270 rows x 2 columns]

In [17]:
model5_results = {
    pdb: {
        pocket: {
            "prob": prob,
            "pred": 1 if prob >= 0.5 else 0,
            "label": info[("Label", "label")],
            "max_overlap": overlaps.max(),
            **overlaps["Pockets"].to_dict()
        }
        for pocket in pockets["pocket"]
        for prob in (extra_probs.loc[f"{pdb}_{pocket}", 1],)
        for info in (extra.loc[f"{pdb}_{pocket}"],)
        for overlaps in (info[[("Pockets", "pocket_in_site"), ("Pockets", "site_in_pocket")]],)
    }
    for pdb, pockets in (
        pd.DataFrame(
            extra_probs.index.map(lambda x: x.split("_")).values.tolist(),
            columns=["pdb", "pocket"]
        )
        .groupby("pdb")
    )
}

model5_results

{'4jqi': {'pocket16': {'prob': 0.0001226096646860242,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket18': {'prob': 0.003527346532791853,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket11': {'prob': 4.818243542104028e-05,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket15': {'prob': 1.1008408629109567e-09,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket7': {'prob': 0.0006957116420380771,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket13': {'prob': 0.09678139537572861,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket14': {'prob': 1.2360335688299529e-07,
   'pred': 0,
   'label': 0,
   'max_overl

In [18]:
pd.DataFrame((
    {
        "pdb": pdb,
        "pocket": pocket,
        **pocketd
    }
    for pdb, pockets in model5_results.items()
    for pocket, pocketd in pockets.items()
)).sort_values("max_overlap", ascending=False).iloc[:40]

pdb    pocket          prob  pred  label  max_overlap  \
46               5uak   pocket1  9.867374e-01     1      1     0.962963   
195              7xlq  pocket36  7.707643e-03     0      1     0.950000   
252  AF-A0A1D8PQM9-F1   pocket1  7.636943e-01     1      1     0.904762   
113              6yhr  pocket12  3.283673e-04     0      0     0.750000   
230              8vw5   pocket1  8.185676e-02     0      1     0.695652   
109              6yhr  pocket10  3.061984e-04     0      0     0.692308   
197              7xlq  pocket41  2.944160e-03     0      0     0.533333   
211              8sgj   pocket1  9.810975e-01     1      0     0.531250   
123              7l6r   pocket9  4.967276e-01     0      0     0.526316   
112              6yhr   pocket3  3.484924e-03     0      0     0.411765   
108              6yhr   pocket9  1.037868e-03     0      0     0.388889   
103              6yhr   pocket1  5.116670e-01     1      0     0.379310   
10               4jqi  pocket17  1.322684e-02     0      0     0.300000   
120              7l6r   pocket1  1.644719e-03     0      0     0.300000   
182              7xlq  pocket45  3.081347e-04     0      0     0.300000   
239              8vw5   pocket6  1.372154e-03     0      0     0.260870   
189              7xlq  pocket62  1.469304e-05     0      0     0.250000   
267  AF-A0A1D8PQM9-F1  pocket19  4.550540e-01     0      0     0.250000   
265  AF-A0A1D8PQM9-F1   pocket3  7.510448e-02     0      0     0.238095   
209              8sgj  pocket14  5.787342e-06     0      0     0.222222   
118              7l6r  pocket13  3.898348e-04     0      0     0.222222   
107              6yhr  pocket17  2.264048e-05     0      0     0.214286   
14               4jqi   pocket8  5.881765e-06     0      0     0.200000   
226              8sgj   pocket6  2.534678e-03     0      0     0.187500   
110              6yhr   pocket5  3.163357e-02     0      0     0.166667   
233              8vw5   pocket9  1.554466e-04     0      0     0.142857   
105              6yhr  pocket20  4.259136e-04     0      0     0.142857   
205              8sgj   pocket7  1.997486e-06     0      0     0.125000   
19               5b0u   pocket1  4.594850e-01     0      0     0.125000   
140              7xlq  pocket40  1.387074e-06     0      0     0.125000   
204              8sgj  pocket15  3.372802e-05     0      0     0.111111   
222              8sgj   pocket3  5.811149e-04     0      0     0.105263   
231              8vw5   pocket2  1.656396e-02     0      0     0.105263   
21               5uak  pocket16  3.001944e-05     0      0     0.100000   
7                4jqi   pocket1  4.869621e-01     0      0     0.100000   
13               4jqi   pocket5  1.132708e-03     0      0     0.100000   
161              7xlq  pocket29  1.473504e-08     0      0     0.090909   
215              8sgj   pocket4  3.239725e-04     0      0     0.083333   
179              7xlq  pocket24  1.023644e-03     0      0     0.083333   
92               5uak  pocket36  3.312306e-03     0      0     0.083333   

     pocket_in_site  site_in_pocket  
46         0.139785        0.962963  
195        0.950000        0.655172  
252        0.475000        0.904762  
113        0.750000        0.310345  
230        0.551724        0.695652  
109        0.692308        0.310345  
197        0.533333        0.275862  
211        0.188889        0.531250  
123        0.526316        0.384615  
112        0.411765        0.241379  
108        0.388889        0.241379  
103        0.148649        0.379310  
10         0.125000        0.300000  
120        0.300000        0.115385  
182        0.300000        0.103448  
239        0.250000        0.260870  
189        0.250000        0.103448  
267        0.250000        0.142857  
265        0.185185        0.238095  
209        0.222222        0.062500  
118        0.222222        0.076923  
107        0.214286        0.103448  
14         0.142857        0.200000  
226        0.176471        0.1

# Results

## AllositePro

In [19]:
allositepro_resultsf = "AllositePro/allositepro_results.pkl"

with open(allositepro_resultsf, "rb") as f:
    allositepro_results = {k: v for k,v in pickle.load(f).items() if k in news}

len(allositepro_results), allositepro_results

(2,
 {'7l6r': {'pocket0': {'Volume': 2222.145,
    'SASA': 1065.897,
    'Druggability Score': 0.576,
    'logitProb': 0.844,
    'nmaScore': 0.971,
    'hitScore': 0.869,
    'residues':    auth_asym_id auth_seq_id
    0             A        6972
    1             A        6935
    2             A        6996
    3             A        6947
    4             A        6932
    5             A        6931
    6             A        6999
    7             A        6913
    8             A        6897
    9             A        6824
    10            A        6946
    11            A        6871
    12            A        6896
    13            A        6872
    14            A        6911
    15            A        6844
    16            A        6823
    17            A        6929
    18            A        6971
    19            A        6822
    20            A        6828
    21            A        6841
    22            A        6912
    23            A        6928
    24          

All output pockets are predicted positive.

In [20]:
allositepro_results = {
    pdb: {
        pocket: {
            "pred": 1,
            **pocketd
        }
        for pocket, pocketd in pockets.items()
    }
    for pdb, pockets in allositepro_results.items()
}
allositepro_results

{'7l6r': {'pocket0': {'pred': 1,
   'Volume': 2222.145,
   'SASA': 1065.897,
   'Druggability Score': 0.576,
   'logitProb': 0.844,
   'nmaScore': 0.971,
   'hitScore': 0.869,
   'residues':    auth_asym_id auth_seq_id
   0             A        6972
   1             A        6935
   2             A        6996
   3             A        6947
   4             A        6932
   5             A        6931
   6             A        6999
   7             A        6913
   8             A        6897
   9             A        6824
   10            A        6946
   11            A        6871
   12            A        6896
   13            A        6872
   14            A        6911
   15            A        6844
   16            A        6823
   17            A        6929
   18            A        6971
   19            A        6822
   20            A        6828
   21            A        6841
   22            A        6912
   23            A        6928
   24            A        6937
   25 

## PASSer

In [21]:
passer_resultsf = "PASSer/passer_results.pkl"

with open(passer_resultsf, "rb") as f:
    passer_results = {k1: {k2: v2 for k2, v2 in v1.items() if k2 in news} for k1, v1 in pickle.load(f).items()}

len(passer_results), tuple(len(v) for v in passer_results.values()), passer_results

(3,
 (9, 9, 9),
 {'ensemble': {'8sgj': {'54': {'prob/score': 46.400259248912334,
     'residues':     auth_asym_id auth_seq_id pdbx_PDB_ins_code
     0              A         712                 ?
     1              A         715                 ?
     3              A         711                 ?
     5              A         237                 ?
     7              A         708                 ?
     8              A         707                 ?
     16             A         761                 ?
     17             A         760                 ?
     20             A         759                 ?
     25             A         236                 ?
     27             A          66                 ?
     30             A         235                 ?
     33             A          63                 ?
     39             A          62                 ?
     44             A         241                 ?
     45             A          69                 ?
     46             A  

Top 3 pockets for each PDB are predicted positive.

In [22]:
passer_results = {
    model: {
        pdb: {
            pocket: {
                "pred": 1 if i <=2 else 0,
                **pocketd
            }
            for i, (pocket, pocketd) in enumerate( 
                sorted(
                    pockets.items(), 
                    key=lambda x: x[-1]["prob/score"], 
                    reverse=True
                )
            )
        }
        for pdb, pockets in pdbs.items()
    }
    for model, pdbs in passer_results.items()
}
passer_results

{'ensemble': {'8sgj': {'54': {'pred': 1,
    'prob/score': 46.400259248912334,
    'residues':     auth_asym_id auth_seq_id pdbx_PDB_ins_code
    0              A         712                 ?
    1              A         715                 ?
    3              A         711                 ?
    5              A         237                 ?
    7              A         708                 ?
    8              A         707                 ?
    16             A         761                 ?
    17             A         760                 ?
    20             A         759                 ?
    25             A         236                 ?
    27             A          66                 ?
    30             A         235                 ?
    33             A          63                 ?
    39             A          62                 ?
    44             A         241                 ?
    45             A          69                 ?
    46             A         232          

## DeepAllo

In [23]:
deepallo_resultsf = "DeepAllo/deepallo_results.pkl"

with open(deepallo_resultsf, "rb") as f:
    deepallo_results = pickle.load(f)

len(deepallo_results), deepallo_results

(9,
 {'8sgj': {0: {'pred': 1,
    'prob': 0.06474058330059052,
    'residues':    auth_asym_id auth_seq_id
    0             A         172
    1             A         827
    2             A          98
    3             A         837
    4             A         210
    5             A         830
    6             A         213
    7             A         103
    8             A         165
    9             A         825
    10            A         102
    11            A         224
    12            A         168
    13            A         244
    14            A         826
    15            A          99
    16            A         840
    17            A         222
    18            A         171
    19            A         833
    20            A         214
    21            A         209
    22            A         836
    23            A          97
    24            A         175
    25            A         829},
   1: {'pred': 1,
    'prob': 0.0645398423075676,
    'resi

In [24]:
deepallo_results = {
    pdb: {
        pocket: {
            "prob": 0, # will be replaced by the real prob of the top3 pockets if it's in pocketd
            **pocketd
        }
        for pocket, pocketd in pockets.items()
    }
    for pdb, pockets in deepallo_results.items()
}
deepallo_results

{'8sgj': {0: {'prob': 0.06474058330059052,
   'pred': 1,
   'residues':    auth_asym_id auth_seq_id
   0             A         172
   1             A         827
   2             A          98
   3             A         837
   4             A         210
   5             A         830
   6             A         213
   7             A         103
   8             A         165
   9             A         825
   10            A         102
   11            A         224
   12            A         168
   13            A         244
   14            A         826
   15            A          99
   16            A         840
   17            A         222
   18            A         171
   19            A         833
   20            A         214
   21            A         209
   22            A         836
   23            A          97
   24            A         175
   25            A         829},
  1: {'prob': 0.0645398423075676,
   'pred': 1,
   'residues':    auth_asym_id auth_seq_id
 

## STINGAllo

In [25]:
stingallo_resultsf = "STINGAllo/stingallo_results.pkl"

with open(stingallo_resultsf, "rb") as f:
    stingallo_results = pickle.load(f)

len(stingallo_results), stingallo_results

(1,
 {'6yhr': {'pocket': {'residues':   auth_asym_id auth_seq_id
    0            A         960}}})

In [26]:
stingallo_results = {
    pdb: {
        pocket: {
            "pred": 1,
            **pocketd
        }
        for pocket, pocketd in pockets.items()
    }
    for pdb, pockets in stingallo_results.items()
}
stingallo_results

{'6yhr': {'pocket': {'pred': 1,
   'residues':   auth_asym_id auth_seq_id
   0            A         960}}}

## AllosES

In [27]:
alloses_resultsf = "AllosES/alloses_results.pkl"

with open(alloses_resultsf, "rb") as f:
    alloses_results = pickle.load(f)

len(alloses_results), alloses_results

(9,
 {'8sgj': {'pocket1': {'pro_ave': 0.4566435782802614,
    'residues':    auth_seq_id auth_asym_id
    0          837            A
    1          172            A
    2          833            A
    3          830            A
    4          829            A
    5          836            A
    6          840            A
    7          210            A
    8           99            A
    9          103            A
    10         214            A
    11         244            A
    12          97            A
    13         825            A
    14         827            A
    15         826            A
    16         168            A
    17         175            A
    18         171            A
    19         102            A
    20         165            A
    21         209            A
    22         213            A
    23          98            A
    24         222            A
    25         224            A},
   'pocket54': {'pro_ave': 0.2878497901019058,
    'residues':  

Positive preds. above 0.5 probability (average) and upper pdb name for AlphaFold model.

In [28]:
alloses_results = {
    pdb if "af" not in pdb.lower() else pdb.upper(): {
        pocket: {
            "pred": 1 if pocketd["pro_ave"] >= 0.5 else 0,
            **pocketd
        }
        for pocket, pocketd in pockets.items()
    }
    for pdb, pockets in alloses_results.items()
}
alloses_results

{'8sgj': {'pocket1': {'pred': 0,
   'pro_ave': 0.4566435782802614,
   'residues':    auth_seq_id auth_asym_id
   0          837            A
   1          172            A
   2          833            A
   3          830            A
   4          829            A
   5          836            A
   6          840            A
   7          210            A
   8           99            A
   9          103            A
   10         214            A
   11         244            A
   12          97            A
   13         825            A
   14         827            A
   15         826            A
   16         168            A
   17         175            A
   18         171            A
   19         102            A
   20         165            A
   21         209            A
   22         213            A
   23          98            A
   24         222            A
   25         224            A},
  'pocket54': {'pred': 0,
   'pro_ave': 0.2878497901019058,
   'residues':    auth

## MEF-AlloSite

In [29]:
import json

In [30]:
mefallosite_resultsf = "MEF-AlloSite/mef-allosite_results.json"

with open(mefallosite_resultsf, "r") as f:
    mefallosite_results = json.load(f)

len(mefallosite_results), mefallosite_results

(9,
 {'8vw5': {'pocket15': {'prob': 0.166392813436687,
    'pred': 0,
    'residues': {'auth_asym_id': ['A', 'A', 'A', 'A', 'A', 'A', 'A'],
     'auth_seq_id': ['50', '53', '54', '57', '78', '79', '82'],
     'pdbx_PDB_ins_code': ['?', '?', '?', '?', '?', '?', '?']}},
   'pocket10': {'prob': 0.0657426134372751,
    'pred': 0,
    'residues': {'auth_asym_id': ['A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A'],
     'auth_seq_id': ['67',
      '68',
      '70',
      '71',
      '72',
      '74',
      '140',
      '143',
      '144',
      '147',
      '268'],
     'pdbx_PDB_ins_code': ['?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?']}},
   'pocket16': {'prob': 0.1929948745916287,
    'pred': 0,
    'residues': {'auth_asym_id': ['A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A'],
     'auth_seq_id': ['69',

In [31]:
mefallosite_results = {
    pdb if "af" not in pdb.lower() else pdb.upper(): {
        pocket: {
            k: v if k != "residues" else pd.DataFrame(v)
            for k, v in pocketd.items()
        }
        for pocket, pocketd in pockets.items()
    } 
    for pdb, pockets in mefallosite_results.items()
}

mefallosite_results

{'8vw5': {'pocket15': {'prob': 0.166392813436687,
   'pred': 0,
   'residues':   auth_asym_id auth_seq_id pdbx_PDB_ins_code
   0            A          50                 ?
   1            A          53                 ?
   2            A          54                 ?
   3            A          57                 ?
   4            A          78                 ?
   5            A          79                 ?
   6            A          82                 ?},
  'pocket10': {'prob': 0.0657426134372751,
   'pred': 0,
   'residues':    auth_asym_id auth_seq_id pdbx_PDB_ins_code
   0             A          67                 ?
   1             A          68                 ?
   2             A          70                 ?
   3             A          71                 ?
   4             A          72                 ?
   5             A          74                 ?
   6             A         140                 ?
   7             A         143                 ?
   8             A         1

## ALLO

In [32]:
allo_resultsf = "ALLO/ALLO_results.json"

with open(allo_resultsf, "r") as f:
    allo_results = json.load(f)

len(allo_results), allo_results

(9,
 {'7xlq': {'P_29': {'pred': 0,
    'prob': 0.02126,
    'residues': {'pdbx_PDB_ins_code': ['?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?'],
     'auth_asym_id': ['A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A'],
     'auth_seq_id': ['128',
      '132',
      '166',
      '167',
      '170',
      '171',
      '174',
      '175',
      '189',
      '190',
      '192',
      '193',
      '196']}},
   'P_28': {'pred': 0,
    'prob': 0.02137,
    'residues': {'pdbx_PDB_ins_code': ['?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?'],
     'auth_asym_id': ['A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A'],
     'auth_seq_id': ['1160',
      '1163',
      '1164',
    

In [33]:
allo_results = {
    pdb: {
        pocket: {
            k: v if k != "residues" else pd.DataFrame(v)
            for k, v in pocketd.items()
        }
        for pocket, pocketd in pockets.items()
    } 
    for pdb, pockets in allo_results.items()
}

allo_results

{'7xlq': {'P_29': {'pred': 0,
   'prob': 0.02126,
   'residues':    pdbx_PDB_ins_code auth_asym_id auth_seq_id
   0                  ?            A         128
   1                  ?            A         132
   2                  ?            A         166
   3                  ?            A         167
   4                  ?            A         170
   5                  ?            A         171
   6                  ?            A         174
   7                  ?            A         175
   8                  ?            A         189
   9                  ?            A         190
   10                 ?            A         192
   11                 ?            A         193
   12                 ?            A         196},
  'P_28': {'pred': 0,
   'prob': 0.02137,
   'residues':    pdbx_PDB_ins_code auth_asym_id auth_seq_id
   0                  ?            A        1160
   1                  ?            A        1163
   2                  ?            A        1164


## All models

In [34]:
defaults = { "all_pockets_in_output": True, "prob_key": "prob" }

models = {
    "model5": { "results": model5_results, **defaults, "labelling": None },
    
    "allositepro": { "results": allositepro_results, "all_pockets_in_output": False, "prob_key": "hitScore" },
    "stingallo": { "results": stingallo_results, "all_pockets_in_output": False, "prob_key": None },
    
    "passer_ensemble": { "results": passer_results["ensemble"], **defaults, "prob_key": "prob/score" },
    "passer_automl": { "results": passer_results["automl"], **defaults, "prob_key": "prob/score" },
    "passer_rank": { "results": passer_results["rank"], **defaults, "prob_key": "prob/score" },
    "deepallo": { "results": deepallo_results, **defaults },
    "alloses": { "results": alloses_results, **defaults, "prob_key": "pro_ave" },
    "mefallosite": { "results": mefallosite_results, **defaults },
    "allo": { "results": allo_results, **defaults },
}
models

{'model5': {'results': {'4jqi': {'pocket16': {'prob': 0.0001226096646860242,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket18': {'prob': 0.003527346532791853,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket11': {'prob': 4.818243542104028e-05,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket15': {'prob': 1.1008408629109567e-09,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket7': {'prob': 0.0006957116420380771,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket13': {'prob': 0.09678139537572861,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.

# Labelling

In [35]:
# Percentage of residues of "one" in "other"
get_overlap = lambda one, other: (
    len( one.merge(other) ) / len(one)
)

get_overlaps = lambda pdb, pocketd: {
    name: get_overlap(*one_in_other) 
        for site in news_sites[pdb] 
            for name, one_in_other in (
                ("pocket_in_site", (pocketd["residues"], site["site"])),
                ("site_in_pocket", (site["site"], pocketd["residues"])),
            )
}

def get_label(overlaps, site_in_pocket=None, pocket_in_site=None):
    assert not (site_in_pocket==None and pocket_in_site==None)
    
    if site_in_pocket is None:
        return int( overlaps["pocket_in_site"] >= pocket_in_site )
    if pocket_in_site is None:
        return int( overlaps["site_in_pocket"] >= site_in_pocket )
    return int( overlaps["site_in_pocket"] >= site_in_pocket or overlaps["pocket_in_site"] >= pocket_in_site )

In [36]:
def label_results(resultsd, site_in_pocket=0.65, pocket_in_site=None, prob_key=None):
    return pd.DataFrame((
        {
            "pdb": pdb,
            "pocket": pocket,
            **{"prob": pocketd[prob_key] for prob_key in (prob_key,) if prob_key is not None},
            "pred": pocketd["pred"],
            "label": get_label(overlaps, site_in_pocket, pocket_in_site),
            "max_overlap": max(overlaps.values()),
            **overlaps,
        }
        for pdb, pockets in resultsd.items()
        for pocket, pocketd in pockets.items()
        for overlaps in (get_overlaps(pdb, pocketd),)
    )).sort_values("max_overlap", ascending=False)

In [37]:
def label_results_topx(resultsd, site_in_pocket=0.65, pocket_in_site=None, prob_key=None):
    df = pd.DataFrame((
        {
            "pdb": pdb,
            "pocket": pocket,
            **{"prob": pocketd[prob_key] for prob_key in (prob_key,) if prob_key is not None},
            "pred": pocketd["pred"],
            "label": get_label(overlaps, site_in_pocket, pocket_in_site),
            "max_overlap": max(overlaps.values()),
            **overlaps,
        }
        for pdb, pockets in resultsd.items()
        for pocket, pocketd in pockets.items()
        for overlaps in (get_overlaps(pdb, pocketd),)
    ))
    if prob_key is not None:
        df["pred"] = (
            # Start from a Series where each value/row (sample/pocket) is the total number of pos. labels on its PDB
            df.groupby("pdb")["label"].transform("sum")
            # Then subtract this "total num. of pos. in a PDB" by the rank of each pocket in a PDB, sorted by the probability
            .sub(df.groupby("pdb")["prob"].rank(method="first", ascending=False))
            # If the subtraction is positive or 0 it means that the pocket is in the topX and will be assigned 1
            >= 0
        ).astype(int)
        # If a PDB has no + labelled pocket, assign the highest prob. as positive
        for pdb, group in df.groupby("pdb"):
            if group["pred"].sum() == 0:
                df.loc[ group["prob"].idxmax(), "pred" ] = 1
            
    
    return df.sort_values("site_in_pocket", ascending=False)

## Our results

In [38]:
def label_our_results(resultsd, site_in_pocket=0.65, pocket_in_site=None):
    return pd.DataFrame((
        {
            "pdb": pdb,
            "pocket": pocket,
            "prob": pocketd["prob"],
            "pred": pocketd["pred"],
            "pred_top1": int( pocketd["prob"] == pdb_maxprob ),
            "label": get_label(overlaps, site_in_pocket, pocket_in_site),
            "max_overlap": max(overlaps.values()),
            **overlaps,
        }
        for pdb, pockets in resultsd.items()
        for pdb_maxprob in (max(pktd["prob"] for pktd in pockets.values()),)
        for pocket, pocketd in pockets.items()
        for overlaps in ({k: pocketd[k] for k in ["pocket_in_site", "site_in_pocket"]},)
    )).sort_values("max_overlap", ascending=False)


def label_our_results_topx(resultsd, site_in_pocket=0.65, pocket_in_site=None):
    df = pd.DataFrame((
        {
            "pdb": pdb,
            "pocket": pocket,
            "prob": pocketd["prob"],
            "label": get_label(overlaps, site_in_pocket, pocket_in_site),
            "max_overlap": max(overlaps.values()),
            **overlaps,
        }
        for pdb, pockets in resultsd.items()
        for pocket, pocketd in pockets.items()
        for overlaps in ({k: pocketd[k] for k in ["pocket_in_site", "site_in_pocket"]},)
    ))
    df["pred"] = (
        # Start from a Series where each value/row (sample/pocket) is the total number of pos. labels on its PDB
        df.groupby("pdb")["label"].transform("sum")
        # Then subtract this "total num. of pos. in a PDB" by the rank of each pocket in a PDB, sorted by the probability
        .sub(df.groupby("pdb")["prob"].rank(method="first", ascending=False))
        # If the subtraction is positive or 0 it means that the pocket is in the topX and will be assigned 1
        >= 0
    ).astype(int)
    # If a PDB has no + labelled pocket, assign the highest prob. as positive
    for pdb, group in df.groupby("pdb"):
        if group["pred"].sum() == 0:
            df.loc[ group["prob"].idxmax(), "pred" ] = 1

    
    # ########## TEMP top1 labelling
    # df["pred"] = 0
    # for pdb, group in df.groupby("pdb"):
    #     df.loc[ group["prob"].idxmax(), "pred" ] = 1


    return df.sort_values("site_in_pocket", ascending=False)

In [39]:
label_our_results_topx(model5_results, site_in_pocket=0.35, pocket_in_site=None,).iloc[:40].sort_values("site_in_pocket", ascending=False)

pdb    pocket          prob  label  max_overlap  \
46               5uak   pocket1  9.867374e-01      1     0.962963   
252  AF-A0A1D8PQM9-F1   pocket1  7.636943e-01      1     0.904762   
230              8vw5   pocket1  8.185676e-02      1     0.695652   
195              7xlq  pocket36  7.707643e-03      1     0.950000   
211              8sgj   pocket1  9.810975e-01      1     0.531250   
123              7l6r   pocket9  4.967276e-01      1     0.526316   
103              6yhr   pocket1  5.116670e-01      1     0.379310   
109              6yhr  pocket10  3.061984e-04      0     0.692308   
113              6yhr  pocket12  3.283673e-04      0     0.750000   
10               4jqi  pocket17  1.322684e-02      0     0.300000   
197              7xlq  pocket41  2.944160e-03      0     0.533333   
239              8vw5   pocket6  1.372154e-03      0     0.260870   
108              6yhr   pocket9  1.037868e-03      0     0.388889   
112              6yhr   pocket3  3.484924e-03      0     0.411765   
265  AF-A0A1D8PQM9-F1   pocket3  7.510448e-02      0     0.238095   
14               4jqi   pocket8  5.881765e-06      0     0.200000   
226              8sgj   pocket6  2.534678e-03      0     0.187500   
267  AF-A0A1D8PQM9-F1  pocket19  4.550540e-01      0     0.250000   
19               5b0u   pocket1  4.594850e-01      0     0.125000   
120              7l6r   pocket1  1.644719e-03      0     0.300000   
189              7xlq  pocket62  1.469304e-05      0     0.250000   
182              7xlq  pocket45  3.081347e-04      0     0.300000   
107              6yhr  pocket17  2.264048e-05      0     0.214286   
7                4jqi   pocket1  4.869621e-01      0     0.100000   
13               4jqi   pocket5  1.132708e-03      0     0.100000   
233              8vw5   pocket9  1.554466e-04      0     0.142857   
231              8vw5   pocket2  1.656396e-02      0     0.105263   
118              7l6r  pocket13  3.898348e-04      0     0.222222   
92               5uak  pocket36  3.312306e-03      0     0.083333   
110              6yhr   pocket5  3.163357e-02      0     0.166667   
187              7xlq  pocket38  3.379444e-03      0     0.068966   
105              6yhr  pocket20  4.259136e-04      0     0.142857   
209              8sgj  pocket14  5.787342e-06      0     0.222222   
222              8sgj   pocket3  5.811149e-04      0     0.105263   
237              8vw5   pocket3  1.013988e-04      0     0.055556   
122              7l6r   pocket4  6.775619e-04      0     0.071429   
23               5uak  pocket74  8.362493e-02      0     0.037037   
21               5uak  pocket16  3.001944e-05      0     0.100000   
62               5uak  pocket10  8.874721e-07      0     0.071429   
179              7xlq  pocket24  1.023644e-03      0     0.083333   

     pocket_in_site  site_in_pocket  pred  
46         0.139785        0.962963     1  
252        0.475000        0.904762     1  
230        0.551724        0.695652     1  
195        0.950000        0.655172     0  
211        0.188889        0.531250     1  
123        0.526316        0.384615     1  
103        0.148649        0.379310     1  
109        0.692308        0.310345     0  
113        0.750000        0.310345     0  
10         0.125000        0.300000     0  
197        0.533333        0.275862     0  
239        0.250000        0.260870     0  
108        0.388889        0.241379     0  
112        0.411765        0.241379     0  
265        0.185185        0.238095     0  
14         0.142857        0.200000     0  
226        0.176471        0.187500     0  
267        0.250000        0.142857     0  
19         0.071429        0.125000     1  
120        0.300000        0.115385     0  
189        0.250000        0.103448     0  
182        0.300000        0.103448     0  
107        0.214286        0.103448     0  
7          0.016949        0.100000     1  
13         0.100000        0.100000     0  
233        0.142857        0.086957     0  


In [40]:
label_our_results_topx(model5_results, site_in_pocket=0.35, pocket_in_site=None).query("pdb == '7xlq'").sort_values("pred")

pdb    pocket      prob  label  max_overlap  pocket_in_site  \
156  7xlq  pocket44  0.000038      0          0.0             0.0   
180  7xlq  pocket56  0.000104      0          0.0             0.0   
181  7xlq   pocket3  0.001409      0          0.0             0.0   
165  7xlq  pocket17  0.000956      0          0.0             0.0   
146  7xlq  pocket39  0.006792      0          0.0             0.0   
..    ...       ...       ...    ...          ...             ...   
148  7xlq  pocket14  0.082497      0          0.0             0.0   
185  7xlq  pocket68  0.421780      0          0.0             0.0   
184  7xlq  pocket50  0.000163      0          0.0             0.0   
183  7xlq  pocket12  0.001076      0          0.0             0.0   
186  7xlq  pocket48  0.515813      0          0.0             0.0   

     site_in_pocket  pred  
156             0.0     0  
180             0.0     0  
181             0.0     0  
165             0.0     0  
146             0.0     0  
..              ...   ...  
148             0.0     0  
185             0.0     0  
184             0.0     0  
183             0.0     0  
186             0.0     1  

[69 rows x 8 columns]

We don't label any pocket for 5b0u and 4jqi

<br>

In [41]:
label_our_results_topx(model5_results, site_in_pocket=0.5, pocket_in_site=0.5).query("pdb in ['5b0u', '4jqi']")

pdb    pocket          prob  label  max_overlap  pocket_in_site  \
10  4jqi  pocket17  1.322684e-02      0        0.300        0.125000   
14  4jqi   pocket8  5.881765e-06      0        0.200        0.142857   
19  5b0u   pocket1  4.594850e-01      0        0.125        0.071429   
7   4jqi   pocket1  4.869621e-01      0        0.100        0.016949   
13  4jqi   pocket5  1.132708e-03      0        0.100        0.100000   
15  4jqi   pocket3  5.942771e-04      0        0.000        0.000000   
16  4jqi  pocket12  3.218317e-07      0        0.000        0.000000   
17  4jqi  pocket19  6.801011e-05      0        0.000        0.000000   
18  4jqi   pocket6  2.429151e-03      0        0.000        0.000000   
20  5b0u   pocket2  2.489165e-07      0        0.000        0.000000   
0   4jqi  pocket16  1.226097e-04      0        0.000        0.000000   
6   4jqi  pocket14  1.236034e-07      0        0.000        0.000000   
5   4jqi  pocket13  9.678140e-02      0        0.000        0.000000   
2   4jqi  pocket11  4.818244e-05      0        0.000        0.000000   
1   4jqi  pocket18  3.527347e-03      0        0.000        0.000000   
8   4jqi   pocket2  4.993942e-02      0        0.000        0.000000   
9   4jqi   pocket4  3.950250e-04      0        0.000        0.000000   
11  4jqi   pocket9  1.895526e-05      0        0.000        0.000000   
12  4jqi  pocket10  1.577715e-04      0        0.000        0.000000   
3   4jqi  pocket15  1.100841e-09      0        0.000        0.000000   
4   4jqi   pocket7  6.957116e-04      0        0.000        0.000000   

    site_in_pocket  pred  
10           0.300     0  
14           0.200     0  
19           0.125     1  
7            0.100     1  
13           0.100     0  
15           0.000     0  
16           0.000     0  
17           0.000     0  
18           0.000     0  
20           0.000     0  
0            0.000     0  
6            0.000     0  
5            0.000     0  
2            0.000     0  
1            0.000     0  
8            0.000     0  
9            0.000     0  
11           0.000     0  
12           0.000     0  
3            0.000     0  
4            0.000     0

In [42]:
models["model5"]["labelling"] = {"site_in_pocket": 0.35, "pocket_in_site": None}

## AllositePro

In [43]:
label_results_topx(allositepro_results, site_in_pocket=0.3, pocket_in_site=None, prob_key=models["allositepro"]["prob_key"])

pdb   pocket   prob  pred  label  max_overlap  pocket_in_site  \
0  7l6r  pocket0  0.869     1      1     0.307692        0.222222   
1  5b0u  pocket0  0.691     1      0     0.062500        0.043478   

   site_in_pocket  
0        0.307692  
1        0.062500

In [44]:
models["allositepro"]["labelling"] = {"site_in_pocket": 0.3, "pocket_in_site": None}

## PASSer

In [45]:
label_results_topx(passer_results["ensemble"], site_in_pocket=0.35, pocket_in_site=None, prob_key=models["passer_ensemble"]["prob_key"]).iloc[:40]

pdb pocket       prob  pred  label  max_overlap  \
472              4jqi     10   8.165355     0      1     0.875000   
132              8vw5      1  23.869776     0      1     0.652174   
214              7xlq     49  33.348420     0      1     0.947368   
386              5uak     36   6.986749     0      1     0.866667   
2                8sgj      1  41.089868     0      1     0.576923   
108              7l6r      4  48.437128     1      1     0.526316   
153              6yhr     44  43.332845     1      1     0.379310   
354              5uak      8  14.665451     0      0     0.500000   
486              4jqi     23   5.072343     0      0     0.375000   
458              4jqi     33  55.258416     1      0     0.300000   
54   AF-A0A1D8PQM9-F1      2  47.126753     1      0     0.285714   
182              6yhr     32   5.505191     0      0     0.727273   
56   AF-A0A1D8PQM9-F1      4  39.288806     0      0     0.238095   
125              7l6r     19   5.441814     0      0     0.666667   
128              7l6r     20   3.761523     0      0     0.857143   
131              8vw5      2  39.862374     1      0     0.227273   
98   AF-A0A1D8PQM9-F1     16   4.976052     0      0     0.500000   
316              5b0u      7   5.728744     0      0     0.333333   
248              7xlq     98   8.648491     0      0     0.500000   
323              5uak     46  44.899312     0      0     0.190476   
303              7xlq     30   2.919939     0      0     0.444444   
164              6yhr      5  10.876080     0      0     0.285714   
165              6yhr     12   9.911722     0      0     0.571429   
152              8vw5     16   3.359023     0      0     0.600000   
312              5b0u      1  42.800219     1      0     0.125000   
158              6yhr     34  19.634407     0      0     0.230769   
257              7xlq     55   7.260456     0      0     0.600000   
465              4jqi      3  19.248772     0      0     0.100000   
475              4jqi     11   7.472721     0      0     0.111111   
104  AF-A0A1D8PQM9-F1     28   4.317198     0      0     0.250000   
14               8sgj     42  10.732115     0      0     0.333333   
52               8sgj     21   3.556922     0      0     0.750000   
136              8vw5     17  14.861351     0      0     0.166667   
129              7l6r     18   3.575197     0      0     0.250000   
119              7l6r     23   6.619178     0      0     0.333333   
325              5uak    113  39.667736     0      0     0.095238   
448              5uak     73   3.036114     0      0     0.200000   
456              5uak    106   2.280939     0      0     0.250000   
184              6yhr     35   5.374672     0      0     0.285714   
159              6yhr      1  19.392601     0      0     0.181818   

     pocket_in_site  site_in_pocket  
472        0.875000        0.700000  
132        0.652174        0.652174  
214        0.947368        0.620690  
386        0.866667        0.481481  
2          0.576923        0.468750  
108        0.526316        0.384615  
153        0.244444        0.379310  
354        0.500000        0.333333  
486        0.375000        0.300000  
458        0.107143        0.300000  
54         0.250000        0.285714  
182        0.727273        0.275862  
56         0.208333        0.238095  
125        0.666667        0.230769  
128        0.857143        0.230769  
131        0.227273        0.217391  
98         0.500000        0.190476  
316        0.333333        0.187500  
248        0.500000        0.172414  
323        0.190476        0.148148  
303        0.444444        0.137931  
164        0.285714        0.137931  
165        0.571429        0.137931  
152        0.600000        0.130435  
312        0.068966        0.125000  
158        0.230769        0.103448  
257        0.600000        0.103448  
465        0.100000        0.100000  
475        0.111111        0.100000  
104        0.250000        0.095238  
14        

In [46]:
models["passer_ensemble"]["labelling"] = {"site_in_pocket": 0.35, "pocket_in_site": None}

In [47]:
label_results_topx(passer_results["automl"], site_in_pocket=0.35, pocket_in_site=None, prob_key=models["passer_automl"]["prob_key"]).iloc[:40]

pdb pocket       prob  pred  label  max_overlap  \
483              4jqi     10   9.329784     0      1     0.875000   
132              8vw5      1  39.378579     0      1     0.652174   
224              7xlq     49  17.964764     0      1     0.947368   
394              5uak     36  10.363541     0      1     0.866667   
0                8sgj      1  47.945435     1      1     0.576923   
108              7l6r      4  33.784361     1      1     0.526316   
153              6yhr     44  34.799055     1      1     0.379310   
356              5uak      8  14.094754     0      0     0.500000   
472              4jqi     23  12.733860     0      0     0.375000   
459              4jqi     33  30.534288     0      0     0.300000   
54   AF-A0A1D8PQM9-F1      2  45.190383     1      0     0.285714   
167              6yhr     32  13.395784     0      0     0.727273   
55   AF-A0A1D8PQM9-F1      4  37.159441     0      0     0.238095   
123              7l6r     19   9.048991     0      0     0.666667   
120              7l6r     20   9.386284     0      0     0.857143   
131              8vw5      2  39.414130     1      0     0.227273   
99   AF-A0A1D8PQM9-F1     16  10.060037     0      0     0.500000   
317              5b0u      7   8.520442     0      0     0.333333   
234              7xlq     98  14.468664     0      0     0.500000   
322              5uak     46  30.230311     0      0     0.190476   
172              6yhr      5  10.585369     0      0     0.285714   
187              6yhr     12   8.695242     0      0     0.571429   
247              7xlq     30  12.673519     0      0     0.444444   
150              8vw5     16   7.924544     0      0     0.600000   
312              5b0u      1  35.763644     1      0     0.125000   
169              6yhr     34  11.320896     0      0     0.230769   
300              7xlq     55   8.031817     0      0     0.600000   
471              4jqi      3  12.998702     0      0     0.100000   
477              4jqi     11  10.597691     0      0     0.111111   
82   AF-A0A1D8PQM9-F1     28  11.560664     0      0     0.250000   
16               8sgj     42  12.878978     0      0     0.333333   
53               8sgj     21   6.813393     0      0     0.750000   
140              8vw5     17  13.844185     0      0     0.166667   
129              7l6r     23   8.209363     0      0     0.333333   
130              7l6r     18   7.600047     0      0     0.250000   
426              5uak     73   8.596281     0      0     0.200000   
433              5uak    106   8.305124     0      0     0.250000   
329              5uak    113  23.986489     0      0     0.095238   
157              6yhr      1  16.111927     0      0     0.181818   
188              6yhr     39   8.644901     0      0     0.333333   

     pocket_in_site  site_in_pocket  
483        0.875000        0.700000  
132        0.652174        0.652174  
224        0.947368        0.620690  
394        0.866667        0.481481  
0          0.576923        0.468750  
108        0.526316        0.384615  
153        0.244444        0.379310  
356        0.500000        0.333333  
472        0.375000        0.300000  
459        0.107143        0.300000  
54         0.250000        0.285714  
167        0.727273        0.275862  
55         0.208333        0.238095  
123        0.666667        0.230769  
120        0.857143        0.230769  
131        0.227273        0.217391  
99         0.500000        0.190476  
317        0.333333        0.187500  
234        0.500000        0.172414  
322        0.190476        0.148148  
172        0.285714        0.137931  
187        0.571429        0.137931  
247        0.444444        0.137931  
150        0.600000        0.130435  
312        0.068966        0.125000  
169        0.230769        0.103448  
300        0.600000        0.103448  
471        0.100000        0.100000  
477        0.111111        0.100000  
82         0.250000        0.095238  
16        

In [48]:
models["passer_automl"]["labelling"] = {"site_in_pocket": 0.35, "pocket_in_site": None}

In [49]:
models["passer_rank"]["labelling"] = {"site_in_pocket": 0.35, "pocket_in_site": None}

## DeepAllo

In [50]:
label_results_topx(deepallo_results, site_in_pocket=0.35, pocket_in_site=None, prob_key=models["deepallo"]["prob_key"]).iloc[:40]

pdb  pocket      prob  pred  label  max_overlap  \
472              4jqi      17  0.000000     0      1     0.875000   
132              8vw5       0  0.079566     1      1     0.652174   
257              7xlq      63  0.000000     0      1     0.947368   
394              5uak      78  0.000000     0      1     0.866667   
0                8sgj       0  0.064741     1      1     0.576923   
184              6yhr      30  0.000000     0      1     0.379310   
408              5uak      92  0.000000     0      0     0.500000   
479              4jqi      24  0.000000     0      0     0.300000   
459              4jqi       4  0.000000     0      0     0.375000   
54   AF-A0A1D8PQM9-F1       0  0.066090     1      0     0.285714   
176              6yhr      22  0.000000     0      0     0.800000   
100  AF-A0A1D8PQM9-F1      46  0.000000     0      0     0.238095   
117              7l6r       9  0.000000     0      0     0.857143   
124              7l6r      16  0.000000     0      0     0.666667   
133              8vw5       1  0.047621     0      0     0.227273   
113              7l6r       5  0.000000     0      0     0.625000   
55   AF-A0A1D8PQM9-F1       1  0.041132     0      0     0.500000   
315              5b0u       6  0.000000     0      0     0.333333   
273              7xlq      79  0.000000     0      0     0.500000   
385              5uak      69  0.000000     0      0     0.190476   
188              6yhr      34  0.000000     0      0     0.571429   
156              6yhr       2  0.045578     0      0     0.285714   
292              7xlq      98  0.000000     0      0     0.444444   
139              8vw5       7  0.000000     0      0     0.600000   
314              5b0u       5  0.000000     0      0     0.125000   
248              7xlq      54  0.000000     0      0     0.600000   
189              6yhr      35  0.000000     0      0     0.230769   
461              4jqi       6  0.000000     0      0     0.111111   
85   AF-A0A1D8PQM9-F1      31  0.000000     0      0     0.250000   
9                8sgj       9  0.000000     0      0     0.750000   
18               8sgj      18  0.000000     0      0     0.333333   
146              8vw5      14  0.000000     0      0     0.166667   
115              7l6r       7  0.000000     0      0     0.333333   
129              7l6r      21  0.000000     0      0     0.250000   
360              5uak      44  0.000000     0      0     0.095238   
373              5uak      57  0.000000     0      0     0.250000   
376              5uak      60  0.000000     0      0     0.200000   
177              6yhr      23  0.000000     0      0     0.333333   
190              6yhr      36  0.000000     0      0     0.285714   
155              6yhr       1  0.052955     0      0     0.181818   

     pocket_in_site  site_in_pocket  
472        0.875000        0.700000  
132        0.652174        0.652174  
257        0.947368        0.620690  
394        0.866667        0.481481  
0          0.576923        0.468750  
184        0.244444        0.379310  
408        0.500000        0.333333  
479        0.111111        0.300000  
459        0.375000        0.300000  
54         0.250000        0.285714  
176        0.800000        0.275862  
100        0.208333        0.238095  
117        0.857143        0.230769  
124        0.666667        0.230769  
133        0.227273        0.217391  
113        0.625000        0.192308  
55         0.500000        0.190476  
315        0.333333        0.187500  
273        0.500000        0.172414  
385        0.190476        0.148148  
188        0.571429        0.137931  
156        0.285714        0.137931  
292        0.444444        0.137931  
139        0.600000        0.130435  
314        0.068966        0.125000  
248        0.600000        0.103448  
189        0.230769        0.103448  
461        0.111111        0.100000  
85         0.250000        0.095238  
9          0.750000        0.093750  
18        

In [51]:
models["deepallo"]["labelling"] = {"site_in_pocket": 0.35, "pocket_in_site": None}

## STINGAllo

In [52]:
label_results_topx(stingallo_results, site_in_pocket=None, pocket_in_site=1)

pdb  pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
0  6yhr  pocket     1      0          0.0             0.0             0.0

In [53]:
models["stingallo"]["labelling"] = {"site_in_pocket": None, "pocket_in_site": 1}

## AllosES

In [54]:
label_results_topx(alloses_results, site_in_pocket=0.35, pocket_in_site=None, prob_key=models["alloses"]["prob_key"]).iloc[:40]

pdb     pocket      prob  pred  label  max_overlap  \
465              4jqi   pocket10  0.085983     0      1     0.875000   
132              8vw5    pocket1  0.209389     0      1     0.652174   
206              7xlq   pocket49  0.234133     0      1     0.947368   
331              5uak   pocket36  0.282710     0      1     0.866667   
0                8sgj    pocket1  0.456644     1      1     0.576923   
108              7l6r    pocket4  0.247076     1      1     0.526316   
153              6yhr   pocket44  0.260430     1      1     0.379310   
359              5uak    pocket8  0.180405     0      0     0.500000   
470              4jqi   pocket23  0.070526     0      0     0.375000   
462              4jqi   pocket33  0.119898     0      0     0.300000   
55   AF-A0A1D8PQM9-F1    pocket2  0.131197     0      0     0.285714   
171              6yhr   pocket32  0.058084     0      0     0.727273   
54   AF-A0A1D8PQM9-F1    pocket4  0.283396     1      0     0.238095   
118              7l6r   pocket19  0.094290     0      0     0.666667   
125              7l6r   pocket20  0.055339     0      0     0.857143   
131              8vw5    pocket2  0.233149     1      0     0.227273   
71   AF-A0A1D8PQM9-F1   pocket16  0.054414     0      0     0.500000   
315              5b0u    pocket7  0.078701     0      0     0.333333   
239              7xlq   pocket98  0.106500     0      0     0.500000   
324              5uak   pocket46  0.328534     0      0     0.190476   
222              7xlq   pocket30  0.148093     0      0     0.444444   
166              6yhr    pocket5  0.073085     0      0     0.285714   
185              6yhr   pocket12  0.042729     0      0     0.571429   
151              8vw5   pocket16  0.038916     0      0     0.600000   
312              5b0u    pocket1  0.441154     1      0     0.125000   
268              7xlq   pocket55  0.064184     0      0     0.600000   
158              6yhr   pocket34  0.105171     0      0     0.230769   
471              4jqi    pocket3  0.066144     0      0     0.100000   
463              4jqi   pocket11  0.091624     0      0     0.111111   
72   AF-A0A1D8PQM9-F1   pocket28  0.053928     0      0     0.250000   
12               8sgj   pocket21  0.119245     0      0     0.750000   
43               8sgj   pocket42  0.050845     0      0     0.333333   
139              8vw5   pocket17  0.075004     0      0     0.166667   
119              7l6r   pocket18  0.088039     0      0     0.250000   
129              7l6r   pocket23  0.044034     0      0     0.333333   
397              5uak  pocket106  0.121576     0      0     0.250000   
342              5uak  pocket113  0.208573     0      0     0.095238   
387              5uak   pocket73  0.129385     0      0     0.200000   
156              6yhr    pocket1  0.124235     0      0     0.181818   
190              6yhr   pocket35  0.033142     0      0     0.285714   

     pocket_in_site  site_in_pocket  
465        0.875000        0.700000  
132        0.652174        0.652174  
206        0.947368        0.620690  
331        0.866667        0.481481  
0          0.576923        0.468750  
108        0.526316        0.384615  
153        0.244444        0.379310  
359        0.500000        0.333333  
470        0.375000        0.300000  
462        0.107143        0.300000  
55         0.250000        0.285714  
171        0.727273        0.275862  
54         0.208333        0.238095  
118        0.666667        0.230769  
125        0.857143        0.230769  
131        0.227273        0.217391  
71         0.500000        0.190476  
315        0.333333        0.187500  
239        0.500000        0.172414  
324        0.190476        0.148148  
222        0.444444        0.137931  
166        0.285714        0.137931  
185        0.571429        0.137931  
151        0.600000        0.130435  
312        0.068966        0.125000  
268        0.600000        0.103448  
158        0.230769        0.103448  
4

In [55]:
models["alloses"]["labelling"] = {"site_in_pocket": 0.35, "pocket_in_site": None}

## MEF-AlloSite

In [56]:
label_results_topx(mefallosite_results, site_in_pocket=0.35, pocket_in_site=None, prob_key=models["mefallosite"]["prob_key"]).iloc[:40]

pdb     pocket      prob  pred  label  max_overlap  \
413              4jqi    pocket8  0.162924     0      1     0.875000   
11               8vw5    pocket1  0.700402     1      1     0.652174   
173              7xlq   pocket33  0.522724     0      1     0.947368   
358              5uak   pocket35  0.470506     0      1     0.866667   
53               8sgj    pocket1  0.637592     1      1     0.576923   
132              7l6r    pocket4  0.613464     1      1     0.526316   
138              6yhr   pocket33  0.597958     1      1     0.379310   
348              5uak    pocket8  0.494636     0      0     0.500000   
399              4jqi   pocket22  0.054662     0      0     0.375000   
82   AF-A0A1D8PQM9-F1    pocket2  0.388975     0      0     0.285714   
144              6yhr   pocket27  0.093021     0      0     0.727273   
110  AF-A0A1D8PQM9-F1    pocket4  0.631212     0      0     0.238095   
125              7l6r   pocket18  0.071513     0      0     0.666667   
4                8vw5    pocket2  0.665438     0      0     0.227273   
422              4jqi    pocket7  0.619607     0      0     0.200000   
127              7l6r   pocket17  0.061007     0      0     0.833333   
77   AF-A0A1D8PQM9-F1   pocket16  0.057716     0      0     0.500000   
257              5b0u    pocket4  0.059752     0      0     0.333333   
185              7xlq   pocket71  0.071074     0      0     0.500000   
325              5uak   pocket46  0.693293     0      0     0.190476   
166              6yhr   pocket11  0.057327     0      0     0.571429   
209              7xlq   pocket20  0.239346     0      0     0.444444   
164              6yhr    pocket4  0.505853     0      0     0.285714   
10               8vw5   pocket13  0.060015     0      0     0.600000   
256              5b0u    pocket1  0.659194     1      0     0.125000   
157              6yhr   pocket26  0.381438     0      0     0.250000   
250              7xlq   pocket38  0.062914     0      0     0.600000   
406              4jqi   pocket25  0.088113     0      0     0.142857   
400              4jqi   pocket10  0.061915     0      0     0.142857   
421              4jqi   pocket11  0.141477     0      0     0.111111   
95   AF-A0A1D8PQM9-F1   pocket28  0.058527     0      0     0.250000   
44               8sgj   pocket36  0.063888     0      0     0.333333   
38               8sgj   pocket18  0.059533     0      0     0.750000   
1                8vw5   pocket10  0.065743     0      0     0.181818   
120              7l6r   pocket16  0.077571     0      0     0.250000   
313              5uak  pocket106  0.054786     0      0     0.250000   
316              5uak   pocket73  0.086120     0      0     0.200000   
300              5uak  pocket113  0.676112     0      0     0.095238   
162              6yhr    pocket1  0.480399     0      0     0.181818   
28               8sgj   pocket43  0.457890     0      0     0.166667   

     pocket_in_site  site_in_pocket  
413        0.875000        0.700000  
11         0.652174        0.652174  
173        0.947368        0.620690  
358        0.866667        0.481481  
53         0.576923        0.468750  
132        0.526316        0.384615  
138        0.255814        0.379310  
348        0.500000        0.333333  
399        0.375000        0.300000  
82         0.250000        0.285714  
144        0.727273        0.275862  
110        0.208333        0.238095  
125        0.666667        0.230769  
4          0.227273        0.217391  
422        0.086957        0.200000  
127        0.833333        0.192308  
77         0.500000        0.190476  
257        0.333333        0.187500  
185        0.500000        0.172414  
325        0.190476        0.148148  
166        0.571429        0.137931  
209        0.444444        0.137931  
164        0.285714        0.137931  
10         0.600000        0.130435  
256        0.068966        0.125000  
157        0.250000        0.103448  
250        0.600000        0.103448  
4

In [57]:
models["mefallosite"]["labelling"] = {"site_in_pocket": 0.35, "pocket_in_site": None}

## ALLO

In [58]:
label_results_topx(allo_results, site_in_pocket=0.38, pocket_in_site=None, prob_key=models["allo"]["prob_key"]).iloc[:40]

pdb pocket     prob  pred  label  max_overlap  \
204              8vw5    P_0  0.04440     1      1     0.913043   
91   AF-A0A1D8PQM9-F1    P_1  0.02547     0      1     0.904762   
178              5uak    P_0  0.02725     1      1     0.814815   
221              6yhr    P_0  0.10181     1      1     0.689655   
54               7xlq    P_2  0.02505     0      1     0.689655   
112              8sgj    P_1  0.03776     1      1     0.562500   
126              7l6r    P_1  0.02268     0      1     0.384615   
206              5b0u    P_0  0.07064     1      0     0.375000   
90   AF-A0A1D8PQM9-F1    P_0  0.06321     1      0     0.333333   
194              4jqi    P_2  0.02153     0      0     0.300000   
71   AF-A0A1D8PQM9-F1   P_13  0.02131     0      0     0.461538   
117              7l6r    P_8  0.02116     0      0     0.777778   
164              5uak   P_33  0.02132     0      0     0.411765   
222              6yhr    P_1  0.02156     0      0     0.241379   
184              4jqi   P_14  0.02119     0      0     0.200000   
129              5uak   P_21  0.02126     0      0     0.312500   
202              8vw5    P_2  0.02144     0      0     0.190476   
217              6yhr    P_4  0.02148     0      0     0.190476   
18               7xlq   P_41  0.02134     0      0     0.500000   
108              8sgj    P_5  0.02214     0      0     0.142857   
183              4jqi   P_13  0.02114     0      0     0.100000   
109              8sgj    P_2  0.02427     0      0     0.100000   
125              7l6r    P_0  0.02173     0      0     0.076923   
177              5uak    P_3  0.02410     0      0     0.074074   
132              5uak   P_22  0.02130     0      0     0.090909   
50               7xlq    P_6  0.02175     0      0     0.083333   
215              6yhr    P_6  0.02181     0      0     0.166667   
106              8sgj    P_7  0.02144     0      0     0.090909   
105              8sgj    P_6  0.02431     0      0     0.062500   
100              8sgj   P_18  0.02190     0      0     0.117647   
205              8vw5    P_1  0.02156     0      0     0.055556   
123              7l6r    P_2  0.02128     0      0     0.047619   
146              5uak   P_40  0.02148     0      0     0.062500   
150              5uak   P_37  0.02116     0      0     0.111111   
154              5uak   P_13  0.02133     0      0     0.071429   
3                7xlq   P_20  0.02139     0      0     0.066667   
220              6yhr    P_3  0.02156     0      0     0.040000   
37               7xlq   P_33  0.02123     0      0     0.071429   
49               7xlq    P_9  0.02144     0      0     0.052632   
20               7xlq   P_38  0.02117     0      0     0.125000   

     pocket_in_site  site_in_pocket  
204        0.355932        0.913043  
91         0.395833        0.904762  
178        0.366667        0.814815  
221        0.229885        0.689655  
54         0.689655        0.689655  
112        0.315789        0.562500  
126        0.344828        0.384615  
206        0.103448        0.375000  
90         0.140000        0.333333  
194        0.115385        0.300000  
71         0.461538        0.285714  
117        0.777778        0.269231  
164        0.411765        0.259259  
222        0.241379        0.241379  
184        0.181818        0.200000  
129        0.312500        0.185185  
202        0.190476        0.173913  
217        0.190476        0.137931  
18         0.500000        0.137931  
108        0.142857        0.125000  
183        0.090909        0.100000  
109        0.100000        0.093750  
125        0.068966        0.076923  
177        0.066667        0.074074  
132        0.090909        0.074074  
50         0.083333        0.068966  
215        0.166667        0.068966  
106        0.090909        0.062500  
105        0.057143        0.062500  
100        0.117647        0.062500  
205        0.055556        0.043478  
123        0.047619        0.038462  
146        0.062

In [59]:
models["allo"]["labelling"] = {"site_in_pocket": 0.38, "pocket_in_site": None}

In [60]:
pd.to_pickle(models, "models_lenient_labelling.pkl")

# Scoring

In [61]:
models_preds = {}

for model, modeld in models.items():
    results = modeld["results"]
    if "model5" not in model:
        labelled_results = label_results_topx(results, **modeld["labelling"], prob_key=modeld["prob_key"])
    else:
        labelled_results = label_our_results_topx(results, **modeld["labelling"])

    preds = {}
    for pdb in news:
        pdbpreds = labelled_results.query(f"pdb == '{pdb}'")
        total = len(pdbpreds)
        if total > 0:
            tp = len( pdbpreds.loc[lambda x: (x["pred"] == 1) & (x["label"] == 1)] )
            fp = len( pdbpreds.loc[lambda x: (x["pred"] == 1) & (x["label"] == 0)] )
            fn = len( pdbpreds.loc[lambda x: (x["pred"] == 0) & (x["label"] == 1)] )
            if tp + fn == 0:
                fn = 1 # There's at least 1 allo. pocket per PDB
        else:
            tp, fp = 0, 0
            fn = 1 # There's at least 1 allo. pocket per PDB

        if total == 0 or not modeld["all_pockets_in_output"]:
            preds[pdb] = {
                "tp": tp,
                "fn": fn,
                "fp": fp
            }
        else:
            preds[pdb] = {
                "total": total,
                "tp": tp,
                "fn": fn,
                "fp": fp
            }

    models_preds[model] = preds

models_preds

{'model5': {'8sgj': {'total': 28, 'tp': 1, 'fn': 0, 'fp': 0},
  'AF-A0A1D8PQM9-F1': {'total': 30, 'tp': 1, 'fn': 0, 'fp': 0},
  '7l6r': {'total': 14, 'tp': 1, 'fn': 0, 'fp': 0},
  '8vw5': {'total': 13, 'tp': 1, 'fn': 0, 'fp': 0},
  '6yhr': {'total': 20, 'tp': 1, 'fn': 0, 'fp': 0},
  '7xlq': {'total': 69, 'tp': 0, 'fn': 1, 'fp': 1},
  '5b0u': {'total': 2, 'tp': 0, 'fn': 1, 'fp': 1},
  '5uak': {'total': 75, 'tp': 1, 'fn': 0, 'fp': 0},
  '4jqi': {'total': 19, 'tp': 0, 'fn': 1, 'fp': 1}},
 'allositepro': {'8sgj': {'tp': 0, 'fn': 1, 'fp': 0},
  'AF-A0A1D8PQM9-F1': {'tp': 0, 'fn': 1, 'fp': 0},
  '7l6r': {'tp': 1, 'fn': 0, 'fp': 0},
  '8vw5': {'tp': 0, 'fn': 1, 'fp': 0},
  '6yhr': {'tp': 0, 'fn': 1, 'fp': 0},
  '7xlq': {'tp': 0, 'fn': 1, 'fp': 0},
  '5b0u': {'tp': 0, 'fn': 1, 'fp': 1},
  '5uak': {'tp': 0, 'fn': 1, 'fp': 0},
  '4jqi': {'tp': 0, 'fn': 1, 'fp': 0}},
 'stingallo': {'8sgj': {'tp': 0, 'fn': 1, 'fp': 0},
  'AF-A0A1D8PQM9-F1': {'tp': 0, 'fn': 1, 'fp': 0},
  '7l6r': {'tp': 0, 'fn': 1,

In [62]:
from sklearn.metrics import matthews_corrcoef, f1_score, confusion_matrix

In [63]:
models_metrics = {}

for model, preds in models_preds.items():
    df = pd.DataFrame(preds).T
    
    if models[model]["all_pockets_in_output"]:
        y_true = [1] * df["tp"].sum() + [1] * df["fn"].sum() + [0] * df["fp"].sum() + [0] * (df["total"].sum() - df[["tp", "fn", "fp"]].sum().sum())
        y_pred = [1] * df["tp"].sum() + [0] * df["fn"].sum() + [1] * df["fp"].sum() + [0] * (df["total"].sum() - df[["tp", "fn", "fp"]].sum().sum())

        models_metrics[model] = {
            "model": model,
            "tp": df["tp"].sum(),
            "fn": df["fn"].sum(),
            "fp": df["fp"].sum(),
            "mcc": matthews_corrcoef(y_true, y_pred),
            "macro-f1": f1_score(y_true, y_pred, average="macro"),
            "confmat": pd.DataFrame(confusion_matrix(y_true, y_pred))
        }
        
    else:
        models_metrics[model] = {
            "model": model,
            "tp": df["tp"].sum(),
            "fn": df["fn"].sum(),
            "fp": df["fp"].sum(),
        }

models_metrics = pd.DataFrame(models_metrics).T.sort_values(["tp", "mcc"], ascending=False)
models_metrics

model tp fn fp       mcc  macro-f1  \
model5                    model5  6  3  3  0.655172  0.827586   
mefallosite          mefallosite  4  5  5  0.432396  0.716198   
allo                        allo  4  5  5   0.42108   0.71054   
passer_automl      passer_automl  3  6  6  0.320885  0.660443   
alloses                  alloses  3  6  6  0.320885  0.660443   
passer_ensemble  passer_ensemble  2  7  7  0.207699   0.60385   
passer_rank          passer_rank  2  7  7  0.207699   0.60385   
deepallo                deepallo  2  7  7  0.207423  0.603712   
allositepro          allositepro  1  8  1       NaN       NaN   
stingallo              stingallo  0  9  1       NaN       NaN   

                                       confmat  
model5                0  1
0  258  3
1    3  6  
mefallosite           0  1
0  410  5
1    5  4  
allo                  0  1
0  209  5
1    5  4  
passer_automl         0  1
0  476  6
1    6  3  
alloses               0  1
0  476  6
1    6  3  
passer_ensemble       0  1
0  475  7
1    7  2  
passer_rank           0  1
0  475  7
1    7  2  
deepallo              0  1
0  466  7
1    7  2  
allositepro                                NaN  
stingallo                                  NaN

In [64]:
models_metrics.infer_objects().to_csv("models_metrics_top1_apos_lenient_labelling.csv", index=False, sep=";", decimal=",")